In [13]:
import pandas as pd

file_path = 'kaz_pop_years.xlsx'
xls = pd.ExcelFile(file_path)

def process_sheet(sheet_name):
    df = xls.parse(sheet_name)
    
    # Extract column headers from row 4 (fixing NaN columns)
    columns = ['Region'] + [str(col).strip().lower() for col in df.iloc[4, 1:].values]
    
    # Ensure columns are correctly assigned, handling any potential NaN or empty headers
    cleaned_df = df.iloc[6:, :].copy()  # Start data from row 6 (after header)
    cleaned_df.columns = columns

    # Add Population Type for Total, Urban, Rural population (based on row positions)
    cleaned_df.loc[7:27, 'population type'] = 'Total'
    cleaned_df.loc[29:48, 'population type'] = 'Urban'
    cleaned_df.loc[51:, 'population type'] = 'Rural'

    cleaned_df['population type'] = cleaned_df['population type'].fillna('Unknown')
    
    # Drop rows that don't contain any numeric data (e.g., rows with '-')
    cleaned_df = cleaned_df[
        cleaned_df.apply(lambda row: pd.to_numeric(row, errors='coerce').notna().any(), axis=1)
    ].reset_index(drop=True)

    # Replace placeholders like '-' with NaN and ensure numeric types for year columns
    cleaned_df.replace('-', None, inplace=True)
    for year in columns[1:]:  # Skip 'Region' column
        cleaned_df[year] = pd.to_numeric(cleaned_df[year], errors='coerce')
    cleaned_df.columns = cleaned_df.columns.str.lower()

    cleaned_df.columns = cleaned_df.columns.map(str).str.strip().str.lower()
    cleaned_df['region'] = cleaned_df['region'].str.strip().str.lower()
    cleaned_df['population type'] = cleaned_df['population type'].str.strip().str.lower()

    # Convert year columns (e.g., 2022.0) to string format (e.g., '2022')
    cleaned_df.columns = [
        str(int(float(col))) if col.replace('.', '', 1).isdigit() else col for col in cleaned_df.columns
    ]

    cleaned_df = cleaned_df[cleaned_df['region'] != 'republic of kazakhstan']
    return cleaned_df

all_population = process_sheet('All population')
men_population = process_sheet('Men')
women_population = process_sheet('Women')

print("\nPreview of all_population data:")
print(all_population)


Preview of all_population data:
                  region       2000       2001       2002       2003  \
1                   abay        NaN        NaN        NaN        NaN   
2                 akmola   799179.0   776377.0   755000.0   748167.0   
3                 aktobe   677715.0   670231.0   668166.0   668378.0   
4                 almaty  1557141.0  1554320.0  1554573.0  1560267.0   
5                 atyrau   441692.0   443630.0   447634.0   451928.0   
6       batys kazakhstan   609161.0   601648.0   600330.0   602133.0   
7                zhambyl   986144.0   981928.0   979199.0   980072.0   
8                zhetisu        NaN        NaN        NaN        NaN   
9              karagandy  1390454.0  1364781.0  1344244.0  1333656.0   
10              kostanay   988787.0   959274.0   935717.0   919558.0   
11             kyzylorda   598526.0   599738.0   600972.0   603804.0   
12             mangistau   315203.0   319191.0   328265.0   338612.0   
13              pavlodar   7907

In [5]:
import json

def normalize_geojson(geojson_file_path):
    """Normalize GeoJSON region names and clean unnecessary fields."""
    with open(geojson_file_path, 'r') as f:
        geojson_data = json.load(f)

    # Standardize region names
    for feature in geojson_data['features']:
        # Normalize the 'name' property
        feature['properties']['name'] = feature['properties']['name'].strip().lower()
        
        # Optionally clean other properties if needed
        # Example: Remove fields like 'id' if not required
        # feature['properties'].pop('id', None)

    return geojson_data

# Path to your GeoJSON file
geojson_file_path = 'kazakhstan_regions.json'

# Normalize the GeoJSON file
normalized_geojson = normalize_geojson(geojson_file_path)
with open('normalized_geojson.geojson', 'w') as f:
    json.dump(normalized_geojson, f, indent=4) 

print("GeoJSON normalization complete.")

GeoJSON normalization complete.


In [7]:
# Verify if the regions match now
print("Regions in all_population:")
print(all_population['region'].unique())

print("\nRegions in GeoJSON:")
for feature in normalized_geojson['features'][:]:
    print(feature['properties']['name'])

Regions in all_population:
['abay' 'akmola' 'aktobe' 'almaty' 'atyrau' 'batys kazakhstan' 'zhambyl'
 'zhetisu' 'karagandy' 'kostanay' 'kyzylorda' 'mangistau' 'pavlodar'
 'soltustik kazakhstan' 'turkistan' 'ulytau' 'shygys kazakhstan'
 'astana city' 'almaty city' 'shymkent city' 'zhetysu']

Regions in GeoJSON:
akmola
aktobe
almaty
almaty city
atyrau
abay
zhambyl
ulytau
kostanay
kyzylorda
mangystau
soltustik kazakhstan
astana city
pavlodar
shymkent city
turkistan
batys kazakhstan
karaganda
zhetisu
shygys kazakhstan


In [9]:
##Normalizing geojson of 2000-2022 before new regions were added

In [15]:
import json

# Load and inspect the uploaded GeoJSON file
geojson_file_path = 'ADM_ADM_1.geojson'

with open(geojson_file_path, 'r', encoding='utf-8') as f:
    geojson_data = json.load(f)

# Function to normalize GeoJSON region names
def normalize_old_geojson(geojson_data):
    mapping = {
        "almaty": "almaty",
        "pavlodar": "pavlodar",
        "qostanay": "kostanay",
        "qaraghandy": "karagandy",
        "qyzylorda": "kyzylorda",
        "zhambyl": "zhambyl",
        "aqtöbe": "aktobe",
        "atyrau": "atyrau",
        "mangghystau": "mangistau",
        "north kazakhstan": "soltustik kazakhstan",
        "aqmola": "akmola",
        # Mapping for derived regions (2000-2021 larger regions split into smaller ones)
        "east kazakhstan": "shygys kazakhstan",
        "west kazakhstan": "batys kazakhstan",
        "south kazakhstan": "turkistan",
        # More mappings can be added based on historical regions
    }

    for feature in geojson_data["features"]:
        # Normalize and map the NAME_1 field
        original_name = feature["properties"].get("NAME_1", "").strip().lower()
        feature["properties"]["name"] = mapping.get(original_name, original_name)

    return geojson_data

# Apply normalization to the old GeoJSON data
normalized_old_geojson = normalize_old_geojson(geojson_data)
with open('normalized_old_geojson.geojson', 'w') as f:
    json.dump(normalized_old_geojson, f, indent=4) 

# Check normalized names
normalized_names = [feature["properties"]["name"] for feature in normalized_old_geojson["features"]]
normalized_names



['almaty',
 'akmola',
 'aktobe',
 'atyrau',
 'shygys kazakhstan',
 'mangistau',
 'soltustik kazakhstan',
 'pavlodar',
 'karagandy',
 'kostanay',
 'kyzylorda',
 'turkistan',
 'batys kazakhstan',
 'zhambyl']

In [32]:
##binding geojson_2022 to population data

In [17]:
def add_population_to_geojson(geojson, all_data, men_data, women_data):
    for feature in geojson['features']:
        region_name = feature['properties']['name']
        feature['properties']['population'] = {}
        
        # Loop through years, assuming they are extracted correctly from the data
        year_columns = all_data.columns[1:]  # Skip the 'Region' column
        for year in year_columns:
            # Get the population data for the region and year
            total_pop_series = all_data.loc[
                (all_data['region'] == region_name) & 
                (all_data['population type'] == 'total'), str(year)]
            men_pop_series = men_data.loc[
                men_data['region'] == region_name, str(year)]
            women_pop_series = women_data.loc[
                women_data['region'] == region_name, str(year)]
            urban_pop_series = all_data.loc[
                (all_data['region'] == region_name) & 
                (all_data['population type'] == 'urban'), str(year)]
            rural_pop_series = all_data.loc[
                (all_data['region'] == region_name) & 
                (all_data['population type'] == 'rural'), str(year)]
            
            # Safely extract the first value if it exists, or set None
            total_pop = total_pop_series.iloc[0] if not total_pop_series.empty else None
            men_pop = men_pop_series.iloc[0] if not men_pop_series.empty else None
            women_pop = women_pop_series.iloc[0] if not women_pop_series.empty else None
            urban_pop = urban_pop_series.iloc[0] if not urban_pop_series.empty else None
            rural_pop = rural_pop_series.iloc[0] if not rural_pop_series.empty else None
            
            # Add the population data for the year to the GeoJSON properties
            feature['properties']['population'][str(year)] = {
                'Total': total_pop if total_pop is not None else None,
                'Men': men_pop if men_pop is not None else None,
                'Women': women_pop if women_pop is not None else None,
                'Urban': urban_pop if urban_pop is not None else None,
                'Rural': rural_pop if rural_pop is not None else None,
            }

    return geojson


geojson_2022_with_data = add_population_to_geojson(normalized_geojson, all_population, men_population, women_population)

In [19]:
##map display for 2022+

In [21]:
import pandas as pd
import folium

# Function to ensure population data is numeric
def create_choropleth_map(geojson, year, map_center=[48.0, 67.0], zoom=5):
    # Create the base map
    m = folium.Map(location=map_center, zoom_start=zoom)
    
    # Prepare data for the selected year, ensuring values are numeric
    data = {
        feature['properties']['name']: pd.to_numeric(
            feature['properties']['population'].get(str(year), {}).get('Total', None),
            errors='coerce'
        )
        for feature in geojson['features']
    }
    
    # Convert data to DataFrame for compatibility with Folium
    data_df = pd.DataFrame(list(data.items()), columns=['Region', 'Total'])
    data_df.dropna(subset=['Total'], inplace=True)  # Remove regions with missing data
    
    # Add a choropleth layer
    folium.Choropleth(
        geo_data=geojson,
        name='choropleth',
        data=data_df,
        columns=['Region', 'Total'],
        key_on='feature.properties.name',
        fill_color='YlGnBu',  # Color scheme
        fill_opacity=0.7,
        line_opacity=0.2,
        nan_fill_color='gray',  # Color for missing data
        legend_name=f"Total Population ({year})"
    ).add_to(m)

    # Add tooltips and popups
    for feature in geojson['features']:
        region_name = feature['properties']['name']
        year_data = feature['properties']['population'].get(str(year), {})
        tooltip_content = (
            f"<b>Region:</b> {region_name}<br>"
            f"<b>Total Population:</b> {year_data.get('Total', 'N/A')}<br>"
            f"<b>Men:</b> {year_data.get('Men', 'N/A')}<br>"
            f"<b>Women:</b> {year_data.get('Women', 'N/A')}<br>"
            f"<b>Urban:</b> {year_data.get('Urban', 'N/A')}<br>"
            f"<b>Rural:</b> {year_data.get('Rural', 'N/A')}"
        )
        folium.GeoJson(
            feature,
            tooltip=folium.Tooltip(tooltip_content),
            popup=folium.Popup(tooltip_content, max_width=300)
        ).add_to(m)
    
    # Add layer control
    folium.LayerControl().add_to(m)
    
    return m

# Example usage
year = 2023  # Replace with the desired year
choropleth_map = create_choropleth_map(geojson_2022_with_data, year)
choropleth_map

In [31]:
##binding geojson_2021_2022 to population data

In [29]:
def bind_population_to_geojson_2000_2021(geojson, all_data, men_data, women_data):
    # List of regions to exclude
    regions_to_exclude = ["ulytau", "zhetisu", "abay"]

# Filter the data frames
    all_data = all_data[~all_data['region'].isin(regions_to_exclude)].reset_index(drop=True)
    men_data = men_data[~men_data['region'].isin(regions_to_exclude)].reset_index(drop=True)
    women_data = women_data[~women_data['region'].isin(regions_to_exclude)].reset_index(drop=True)

    for feature in geojson['features']:
        region_name = feature['properties']['name']
        feature['properties']['population'] = {}
        
        # Loop through years, assuming they are extracted correctly from the data
        year_columns = all_data.columns[1:]  # Skip the 'Region' column
        for year in year_columns:
            # Get the population data for the region and year
            total_pop_series = all_data.loc[
                (all_data['region'] == region_name) & 
                (all_data['population type'] == 'total'), str(year)]
            men_pop_series = men_data.loc[
                men_data['region'] == region_name, str(year)]
            women_pop_series = women_data.loc[
                women_data['region'] == region_name, str(year)]
            urban_pop_series = all_data.loc[
                (all_data['region'] == region_name) & 
                (all_data['population type'] == 'urban'), str(year)]
            rural_pop_series = all_data.loc[
                (all_data['region'] == region_name) & 
                (all_data['population type'] == 'rural'), str(year)]
            
            # Safely extract the first value if it exists, or set None
            total_pop = total_pop_series.iloc[0] if not total_pop_series.empty else None
            men_pop = men_pop_series.iloc[0] if not men_pop_series.empty else None
            women_pop = women_pop_series.iloc[0] if not women_pop_series.empty else None
            urban_pop = urban_pop_series.iloc[0] if not urban_pop_series.empty else None
            rural_pop = rural_pop_series.iloc[0] if not rural_pop_series.empty else None
            
            # Add the population data for the year to the GeoJSON properties
            feature['properties']['population'][str(year)] = {
                'Total': total_pop if total_pop is not None else None,
                'Men': men_pop if men_pop is not None else None,
                'Women': women_pop if women_pop is not None else None,
                'Urban': urban_pop if urban_pop is not None else None,
                'Rural': rural_pop if rural_pop is not None else None,
            }

    return geojson


geojson_2000_2021_with_data = bind_population_to_geojson_2000_2021(normalized_old_geojson, all_population, men_population, women_population)

In [31]:
import pandas as pd
import folium

# Function to ensure population data is numeric
def create_choropleth_map(geojson, year, map_center=[48.0, 67.0], zoom=5):
    # Create the base map
    m = folium.Map(location=map_center, zoom_start=zoom)
    
    # Prepare data for the selected year, ensuring values are numeric
    data = {
        feature['properties']['name']: pd.to_numeric(
            feature['properties']['population'].get(str(year), {}).get('Total', None),
            errors='coerce'
        )
        for feature in geojson['features']
    }
    
    # Convert data to DataFrame for compatibility with Folium
    data_df = pd.DataFrame(list(data.items()), columns=['Region', 'Total'])
    data_df.dropna(subset=['Total'], inplace=True)  # Remove regions with missing data
    
    # Add a choropleth layer
    folium.Choropleth(
        geo_data=geojson,
        name='choropleth',
        data=data_df,
        columns=['Region', 'Total'],
        key_on='feature.properties.name',
        fill_color='YlGnBu',  # Color scheme
        fill_opacity=0.7,
        line_opacity=0.2,
        nan_fill_color='gray',  # Color for missing data
        legend_name=f"Total Population ({year})"
    ).add_to(m)

    # Add tooltips and popups
    for feature in geojson['features']:
        region_name = feature['properties']['name']
        year_data = feature['properties']['population'].get(str(year), {})
        tooltip_content = (
            f"<b>Region:</b> {region_name}<br>"
            f"<b>Total Population:</b> {year_data.get('Total', 'N/A')}<br>"
            f"<b>Men:</b> {year_data.get('Men', 'N/A')}<br>"
            f"<b>Women:</b> {year_data.get('Women', 'N/A')}<br>"
            f"<b>Urban:</b> {year_data.get('Urban', 'N/A')}<br>"
            f"<b>Rural:</b> {year_data.get('Rural', 'N/A')}"
        )
        folium.GeoJson(
            feature,
            tooltip=folium.Tooltip(tooltip_content),
            popup=folium.Popup(tooltip_content, max_width=300)
        ).add_to(m)
    
    # Add layer control
    folium.LayerControl().add_to(m)
    
    return m

# Example usage
year = 2000  # Replace with the desired year
choropleth_map = create_choropleth_map(geojson_2000_2021_with_data, year)
choropleth_map

In [27]:
import pandas as pd
import folium

def create_choropleth_map_with_year_filter(
    geojson_2000_2021, geojson_2022, year, map_center=[48.0, 67.0], zoom=5
):
    """
    Create a choropleth map that dynamically selects the GeoJSON data 
    based on the year and displays population information.
    """
    # Determine which GeoJSON to use based on the year
    if year >= 2022:
        selected_geojson = geojson_2022
    else:
        selected_geojson = geojson_2000_2021
    
    # Create the base map
    m = folium.Map(location=map_center, zoom_start=zoom)
    
    # Prepare data for the selected year, ensuring values are numeric
    data = {
        feature['properties']['name']: pd.to_numeric(
            feature['properties']['population'].get(str(year), {}).get('Total', None),
            errors='coerce'
        )
        for feature in selected_geojson['features']
    }
    
    # Convert data to DataFrame for compatibility with Folium
    data_df = pd.DataFrame(list(data.items()), columns=['Region', 'Total'])
    data_df.dropna(subset=['Total'], inplace=True)  # Remove regions with missing data
    
    # Add a choropleth layer
    folium.Choropleth(
        geo_data=selected_geojson,
        name='choropleth',
        data=data_df,
        columns=['Region', 'Total'],
        key_on='feature.properties.name',
        fill_color='YlGnBu',  # Color scheme
        fill_opacity=0.7,
        line_opacity=0.2,
        nan_fill_color='gray',  # Color for missing data
        legend_name=f"Total Population ({year})"
    ).add_to(m)
    
    # Add tooltips and popups
    for feature in selected_geojson['features']:
        region_name = feature['properties']['name']
        year_data = feature['properties']['population'].get(str(year), {})
        tooltip_content = (
            f"<b>Region:</b> {region_name}<br>"
            f"<b>Total Population:</b> {year_data.get('Total', 'N/A')}<br>"
            f"<b>Men:</b> {year_data.get('Men', 'N/A')}<br>"
            f"<b>Women:</b> {year_data.get('Women', 'N/A')}<br>"
            f"<b>Urban:</b> {year_data.get('Urban', 'N/A')}<br>"
            f"<b>Rural:</b> {year_data.get('Rural', 'N/A')}"
        )
        folium.GeoJson(
            feature,
            tooltip=folium.Tooltip(tooltip_content),
            popup=folium.Popup(tooltip_content, max_width=300)
        ).add_to(m)
    
    # Add layer control
    folium.LayerControl().add_to(m)
    
    return m


year = 2010  # Replace with the desired year
choropleth_map = create_choropleth_map_with_year_filter(
    geojson_2000_2021_with_data, geojson_2022_with_data, year
)
choropleth_map
